In [1]:
#read the reviews
import pandas as pd
df = pd.read_csv(r"C:\Users\jerem\Documents\ASSIGNMENT1\Scraped_reviews.csv")
df.dropna()


product  \
0      MacBook Air 13.6" Laptop - Apple M2 chip - 8GB...   
1      MacBook Air 13.6" Laptop - Apple M2 chip - 8GB...   
2      MacBook Air 13.6" Laptop - Apple M2 chip - 8GB...   
3      MacBook Air 13.6" Laptop - Apple M2 chip - 8GB...   
4      MacBook Air 13.6" Laptop - Apple M2 chip - 8GB...   
...                                                  ...   
51947  ASUS - ROG Zephyrus 15.6" WQHD 165Hz Gaming La...   
51948  ASUS - ROG Zephyrus 15.6" WQHD 165Hz Gaming La...   
51949  ASUS - ROG Zephyrus 15.6" WQHD 165Hz Gaming La...   
51950  ASUS - ROG Zephyrus 15.6" WQHD 165Hz Gaming La...   
51951  ASUS - ROG Zephyrus 15.6" WQHD 165Hz Gaming La...   

                                                  review  
0      Not the best option. Open a few applications a...  
1      Love how it will unlock by my Apple Watch!! Ea...  
2      Swiftness and fast processing makes it stand o...  
3      This laptop is excellent , it runs smooth and ...  
4      Hi Best Buy Team,\n\nI recently purchased a Ma...  
...                                                  ...  
51947  This was purchased for a friend‘s son who live...  
51948  My first order was faulty but BestBuy replaced...  
51949  I primarily use this laptop for some light gam...  
51950  I wanted a VR ready gaming laptop that could h...  
51951  Great Laptop for work and gaming. Had no issue...  

[51952 rows x 2 columns]

In [2]:
df.sample(5) 

product  \
13760  MacBook Air 13.3" Laptop - Apple M1 chip - 8GB...   
38436  MacBook Pro 13.3" Laptop - Apple M2 chip - 8GB...   
278    MacBook Air 13.6" Laptop - Apple M2 chip - 8GB...   
28503  MacBook Air 13.3" Laptop - Apple M1 chip - 8GB...   
25017  MacBook Air 13.3" Laptop - Apple M1 chip - 8GB...   

                                                  review  
13760  The decision I made Day I bought my airMac was...  
38436  Perfect for son in his freshman year of colleg...  
278    I got this for school and I like it a lot, I b...  
28503  I love it! The color is gorgeous and the shipp...  
25017  Really good and works without issues. I bought...

In [3]:
print(len(df))

51952


In [4]:
df.dtypes

product    object
review     object
dtype: object

In [5]:
new_df = pd.DataFrame()

In [6]:
#Sentence Splitting
from nltk.tokenize import sent_tokenize
from cleantext import clean

product = []
review = []

for index in df.index:
    sentences = sent_tokenize(df.loc[index, 'review'])
    for sentence in sentences:
        product.append(df.loc[index, 'product'])
        review.append(clean(sentence, no_emoji=True))


# append columns to new_df

new_df['product'] = product
new_df['review'] = review



In [8]:
new_df.sample(5) 

product  \
16051   HP - Envy 2-in-1 15.6" Full HD Touch-Screen La...   
103670  HP - Envy 2-in-1 15.6" Full HD Touch-Screen La...   
121436  Samsung - Galaxy Book2 360 13.3" AMOLED Touch ...   
83498   Apple - MacBook Pro 14" Laptop - M2 Pro chip -...   
61019   MacBook Air 13.3" Laptop - Apple M1 chip - 8GB...   

                                                   review  
16051   im waiting on a pen to come in so i can use so...  
103670  i wish more businesses had customer service li...  
121436  i have to say though if you're thinking about ...  
83498   the best macbook i've ever owned and i've owne...  
61019   unfortunately her last one developed a screen ...

In [9]:
print(len(new_df))

132355


In [10]:
#Text Preprocessing for aspect extraction
import string
import emoji
import re
import nltk
from textblob import TextBlob
from nltk.corpus import wordnet
from nltk.metrics import edit_distance
from nltk.stem.porter import PorterStemmer
from nltk.tokenize import word_tokenize

# spacy for lemmatization
import spacy
nlp = spacy.load('en_core_web_sm', disable=['parser', 'ner'])

stopwords = nltk.corpus.stopwords.words('english')

def preprocess(text):
    
    #1. Generating the list of words in the tweet (hastags and other punctuations removed)
    text_blob = TextBlob(text)
    text = ' '.join(text_blob.words)
    
    #2. clean the number 
    text = re.sub(r'[0-9]', '', text)
    
    #3. lower the text
    text = text.lower()
    
    #4. conver the emoji to text form
    text = emoji.demojize(text)
    
    #5. remove punctuation 
    for punctuation in string.punctuation:
        text = text.replace(punctuation, '')
    
    #6. tokenize the text
    text = word_tokenize(text)
    
    #7. remove empty token
    text = [t for t in text if len(t) > 0]
    
    #8. remove non-alphabetical token
    text = [t for t in text if t.isalpha()]
    
    #9. replace the negation token
    replacer  = AntonymReplacer()
    text = replacer.replace_negations(text)
    
    #10. remove the stopwords
    text = [i for i in text if i not in stopwords]
    
    #11. stem the text
    #porter_stemmer = PorterStemmer()
    #text = [porter_stemmer.stem(w) for w in text]
    
    #11. lemmatize the text
    text = lemmatization(text, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])
    
    return text


def lemmatization(sent, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    doc = nlp(" ".join(sent)) 
    texts_out = [token.lemma_ for token in doc if token.pos_ in allowed_postags]
    return texts_out

class AntonymReplacer(object):
    def replace(self, word, pos=None):
        antonyms = set()

        for syn in wordnet.synsets(word, pos=pos):
            for lemma in syn.lemmas():
                for antonym in lemma.antonyms():
                    antonyms.add(antonym.name())

        if len(antonyms) == 1:
            return antonyms.pop()
        else:
            return None

    def replace_negations(self, sent):
        i, l = 0, len(sent)
        words = []

        while i < l:
            word = sent[i]

            if word == 'not' and i+1 < l:
                ant = self.replace(sent[i+1])

                if ant:
                    words.append(ant)
                    i += 2
                    continue

            words.append(word)
            i += 1

        return words

In [14]:
#Preprocess the input data
cleaned_text = []
counter = 1

for text in new_df["review"]:
    print(f'Preprocessing row {counter}')
    counter+=1
    cleaned_text.append(preprocess(str(text)))

new_df["Clean"] = cleaned_text
new_df = new_df.dropna()

new_df.to_csv(r"C:\Users\jerem\Documents\ASSIGNMENT1\Preprocessed_Scraped_reviews.csv")
print('Preprocessing done.')

Preprocessing row 1
Preprocessing row 2
Preprocessing row 3
Preprocessing row 4
Preprocessing row 5
Preprocessing row 6
Preprocessing row 7
Preprocessing row 8
Preprocessing row 9
Preprocessing row 10
Preprocessing row 11
Preprocessing row 12
Preprocessing row 13
Preprocessing row 14
Preprocessing row 15
Preprocessing row 16
Preprocessing row 17
Preprocessing row 18
Preprocessing row 19
Preprocessing row 20
Preprocessing row 21
Preprocessing row 22
Preprocessing row 23
Preprocessing row 24
Preprocessing row 25
Preprocessing row 26
Preprocessing row 27
Preprocessing row 28
Preprocessing row 29
Preprocessing row 30
Preprocessing row 31
Preprocessing row 32
Preprocessing row 33
Preprocessing row 34
Preprocessing row 35
Preprocessing row 36
Preprocessing row 37
Preprocessing row 38
Preprocessing row 39
Preprocessing row 40
Preprocessing row 41
Preprocessing row 42
Preprocessing row 43
Preprocessing row 44
Preprocessing row 45
Preprocessing row 46
Preprocessing row 47
Preprocessing row 48
P

Preprocessing row 442
Preprocessing row 443
Preprocessing row 444
Preprocessing row 445
Preprocessing row 446
Preprocessing row 447
Preprocessing row 448
Preprocessing row 449
Preprocessing row 450
Preprocessing row 451
Preprocessing row 452
Preprocessing row 453
Preprocessing row 454
Preprocessing row 455
Preprocessing row 456
Preprocessing row 457
Preprocessing row 458
Preprocessing row 459
Preprocessing row 460
Preprocessing row 461
Preprocessing row 462
Preprocessing row 463
Preprocessing row 464
Preprocessing row 465
Preprocessing row 466
Preprocessing row 467
Preprocessing row 468
Preprocessing row 469
Preprocessing row 470
Preprocessing row 471
Preprocessing row 472
Preprocessing row 473
Preprocessing row 474
Preprocessing row 475
Preprocessing row 476
Preprocessing row 477
Preprocessing row 478
Preprocessing row 479
Preprocessing row 480
Preprocessing row 481
Preprocessing row 482
Preprocessing row 483
Preprocessing row 484
Preprocessing row 485
Preprocessing row 486
Preprocess

Preprocessing row 829
Preprocessing row 830
Preprocessing row 831
Preprocessing row 832
Preprocessing row 833
Preprocessing row 834
Preprocessing row 835
Preprocessing row 836
Preprocessing row 837
Preprocessing row 838
Preprocessing row 839
Preprocessing row 840
Preprocessing row 841
Preprocessing row 842
Preprocessing row 843
Preprocessing row 844
Preprocessing row 845
Preprocessing row 846
Preprocessing row 847
Preprocessing row 848
Preprocessing row 849
Preprocessing row 850
Preprocessing row 851
Preprocessing row 852
Preprocessing row 853
Preprocessing row 854
Preprocessing row 855
Preprocessing row 856
Preprocessing row 857
Preprocessing row 858
Preprocessing row 859
Preprocessing row 860
Preprocessing row 861
Preprocessing row 862
Preprocessing row 863
Preprocessing row 864
Preprocessing row 865
Preprocessing row 866
Preprocessing row 867
Preprocessing row 868
Preprocessing row 869
Preprocessing row 870
Preprocessing row 871
Preprocessing row 872
Preprocessing row 873
Preprocess

Preprocessing row 1224
Preprocessing row 1225
Preprocessing row 1226
Preprocessing row 1227
Preprocessing row 1228
Preprocessing row 1229
Preprocessing row 1230
Preprocessing row 1231
Preprocessing row 1232
Preprocessing row 1233
Preprocessing row 1234
Preprocessing row 1235
Preprocessing row 1236
Preprocessing row 1237
Preprocessing row 1238
Preprocessing row 1239
Preprocessing row 1240
Preprocessing row 1241
Preprocessing row 1242
Preprocessing row 1243
Preprocessing row 1244
Preprocessing row 1245
Preprocessing row 1246
Preprocessing row 1247
Preprocessing row 1248
Preprocessing row 1249
Preprocessing row 1250
Preprocessing row 1251
Preprocessing row 1252
Preprocessing row 1253
Preprocessing row 1254
Preprocessing row 1255
Preprocessing row 1256
Preprocessing row 1257
Preprocessing row 1258
Preprocessing row 1259
Preprocessing row 1260
Preprocessing row 1261
Preprocessing row 1262
Preprocessing row 1263
Preprocessing row 1264
Preprocessing row 1265
Preprocessing row 1266
Preprocessi

Preprocessing row 1615
Preprocessing row 1616
Preprocessing row 1617
Preprocessing row 1618
Preprocessing row 1619
Preprocessing row 1620
Preprocessing row 1621
Preprocessing row 1622
Preprocessing row 1623
Preprocessing row 1624
Preprocessing row 1625
Preprocessing row 1626
Preprocessing row 1627
Preprocessing row 1628
Preprocessing row 1629
Preprocessing row 1630
Preprocessing row 1631
Preprocessing row 1632
Preprocessing row 1633
Preprocessing row 1634
Preprocessing row 1635
Preprocessing row 1636
Preprocessing row 1637
Preprocessing row 1638
Preprocessing row 1639
Preprocessing row 1640
Preprocessing row 1641
Preprocessing row 1642
Preprocessing row 1643
Preprocessing row 1644
Preprocessing row 1645
Preprocessing row 1646
Preprocessing row 1647
Preprocessing row 1648
Preprocessing row 1649
Preprocessing row 1650
Preprocessing row 1651
Preprocessing row 1652
Preprocessing row 1653
Preprocessing row 1654
Preprocessing row 1655
Preprocessing row 1656
Preprocessing row 1657
Preprocessi

...

Preprocessing row 130537
Preprocessing row 130538
Preprocessing row 130539
Preprocessing row 130540
Preprocessing row 130541
Preprocessing row 130542
Preprocessing row 130543
Preprocessing row 130544
Preprocessing row 130545
Preprocessing row 130546
Preprocessing row 130547
Preprocessing row 130548
Preprocessing row 130549
Preprocessing row 130550
Preprocessing row 130551
Preprocessing row 130552
Preprocessing row 130553
Preprocessing row 130554
Preprocessing row 130555
Preprocessing row 130556
Preprocessing row 130557
Preprocessing row 130558
Preprocessing row 130559
Preprocessing row 130560
Preprocessing row 130561
Preprocessing row 130562
Preprocessing row 130563
Preprocessing row 130564
Preprocessing row 130565
Preprocessing row 130566
Preprocessing row 130567
Preprocessing row 130568
Preprocessing row 130569
Preprocessing row 130570
Preprocessing row 130571
Preprocessing row 130572
Preprocessing row 130573
Preprocessing row 130574
Preprocessing row 130575
Preprocessing row 130576


Preprocessing row 130937
Preprocessing row 130938
Preprocessing row 130939
Preprocessing row 130940
Preprocessing row 130941
Preprocessing row 130942
Preprocessing row 130943
Preprocessing row 130944
Preprocessing row 130945
Preprocessing row 130946
Preprocessing row 130947
Preprocessing row 130948
Preprocessing row 130949
Preprocessing row 130950
Preprocessing row 130951
Preprocessing row 130952
Preprocessing row 130953
Preprocessing row 130954
Preprocessing row 130955
Preprocessing row 130956
Preprocessing row 130957
Preprocessing row 130958
Preprocessing row 130959
Preprocessing row 130960
Preprocessing row 130961
Preprocessing row 130962
Preprocessing row 130963
Preprocessing row 130964
Preprocessing row 130965
Preprocessing row 130966
Preprocessing row 130967
Preprocessing row 130968
Preprocessing row 130969
Preprocessing row 130970
Preprocessing row 130971
Preprocessing row 130972
Preprocessing row 130973
Preprocessing row 130974
Preprocessing row 130975
Preprocessing row 130976


Preprocessing row 131331
Preprocessing row 131332
Preprocessing row 131333
Preprocessing row 131334
Preprocessing row 131335
Preprocessing row 131336
Preprocessing row 131337
Preprocessing row 131338
Preprocessing row 131339
Preprocessing row 131340
Preprocessing row 131341
Preprocessing row 131342
Preprocessing row 131343
Preprocessing row 131344
Preprocessing row 131345
Preprocessing row 131346
Preprocessing row 131347
Preprocessing row 131348
Preprocessing row 131349
Preprocessing row 131350
Preprocessing row 131351
Preprocessing row 131352
Preprocessing row 131353
Preprocessing row 131354
Preprocessing row 131355
Preprocessing row 131356
Preprocessing row 131357
Preprocessing row 131358
Preprocessing row 131359
Preprocessing row 131360
Preprocessing row 131361
Preprocessing row 131362
Preprocessing row 131363
Preprocessing row 131364
Preprocessing row 131365
Preprocessing row 131366
Preprocessing row 131367
Preprocessing row 131368
Preprocessing row 131369
Preprocessing row 131370


Preprocessing row 131721
Preprocessing row 131722
Preprocessing row 131723
Preprocessing row 131724
Preprocessing row 131725
Preprocessing row 131726
Preprocessing row 131727
Preprocessing row 131728
Preprocessing row 131729
Preprocessing row 131730
Preprocessing row 131731
Preprocessing row 131732
Preprocessing row 131733
Preprocessing row 131734
Preprocessing row 131735
Preprocessing row 131736
Preprocessing row 131737
Preprocessing row 131738
Preprocessing row 131739
Preprocessing row 131740
Preprocessing row 131741
Preprocessing row 131742
Preprocessing row 131743
Preprocessing row 131744
Preprocessing row 131745
Preprocessing row 131746
Preprocessing row 131747
Preprocessing row 131748
Preprocessing row 131749
Preprocessing row 131750
Preprocessing row 131751
Preprocessing row 131752
Preprocessing row 131753
Preprocessing row 131754
Preprocessing row 131755
Preprocessing row 131756
Preprocessing row 131757
Preprocessing row 131758
Preprocessing row 131759
Preprocessing row 131760


Preprocessing row 132113
Preprocessing row 132114
Preprocessing row 132115
Preprocessing row 132116
Preprocessing row 132117
Preprocessing row 132118
Preprocessing row 132119
Preprocessing row 132120
Preprocessing row 132121
Preprocessing row 132122
Preprocessing row 132123
Preprocessing row 132124
Preprocessing row 132125
Preprocessing row 132126
Preprocessing row 132127
Preprocessing row 132128
Preprocessing row 132129
Preprocessing row 132130
Preprocessing row 132131
Preprocessing row 132132
Preprocessing row 132133
Preprocessing row 132134
Preprocessing row 132135
Preprocessing row 132136
Preprocessing row 132137
Preprocessing row 132138
Preprocessing row 132139
Preprocessing row 132140
Preprocessing row 132141
Preprocessing row 132142
Preprocessing row 132143
Preprocessing row 132144
Preprocessing row 132145
Preprocessing row 132146
Preprocessing row 132147
Preprocessing row 132148
Preprocessing row 132149
Preprocessing row 132150
Preprocessing row 132151
Preprocessing row 132152


In [15]:
print(type(cleaned_text))

<class 'list'>


In [1]:
#Extract 100k from original dataset for BERTopic, skip this if the dataset is < 100k
import pandas as pd
pd.read_csv(r"C:\Users\jerem\Documents\ASSIGNMENT1\Preprocessed_Scraped_reviews.csv").sample(n=100000).to_csv("Extracted_data.csv", index=False)

In [2]:
import pandas as pd
#extracted_data = pd.read_excel("D:/research/data/reviews/extracted_data.xlsx")
extracted_data = pd.read_csv(r"C:\Users\jerem\Documents\ASSIGNMENT1\Preprocessed_Scraped_reviews.csv")

In [3]:
#LDA model training

import gensim.corpora as corpora
import gensim.models as models

from ast import literal_eval
from pprint import pprint

data_words = []
for x in extracted_data['Clean']:
    data_words.append(literal_eval(x))

# Create Dictionary
id2word = corpora.Dictionary(data_words)
# Create Corpus
texts = data_words
# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# number of topics
num_topics = 50
num_words = 10

# Build LDA model
lda_model1 =models.LdaMulticore(corpus=corpus,
                              id2word=id2word,
                              num_topics=num_topics)



C:\Users\jerem\anaconda3\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.26.1
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [4]:
#save LDA Model
import pickle
topics = lda_model1.print_topics(num_topics=num_topics, num_words=num_words)
topic_list = []
for topic in topics:
  topic_list.append(topic[1])

#df['topics1'] = topic_list1
df_topics = pd.DataFrame(topic_list,  columns =['topics'])
folder1 =r"C:\Users\jerem\Documents\ASSIGNMENT1" 

df_topics.to_csv(f"{folder1}LDA_topics.csv")
pickle.dump(lda_model1, open(f'{folder1}LDA_model.model', 'wb'))#save lda model
pickle.dump(id2word, open(f'{folder1}LDA_model.dict', 'wb'))#save dictionary
pickle.dump(corpus, open(f'{folder1}LDA_model.corpus', 'wb'))#save corpus



In [5]:
pprint(lda_model1.print_topics())
doc_lda = lda_model1[corpus]

[(3,
  '0.042*"laptop" + 0.028*"use" + 0.024*"computer" + 0.020*"buy" + '
  '0.020*"work" + 0.019*"purchase" + 0.017*"time" + 0.016*"good" + '
  '0.015*"long" + 0.014*"problem"'),
 (32,
  '0.085*"price" + 0.085*"good" + 0.040*"great" + 0.038*"product" + '
  '0.034*"buy" + 0.029*"excellent" + 0.024*"laptop" + 0.020*"get" + '
  '0.013*"time" + 0.013*"battery"'),
 (11,
  '0.048*"laptop" + 0.035*"look" + 0.024*"upgrade" + 0.021*"great" + '
  '0.018*"need" + 0.017*"computer" + 0.016*"feel" + 0.012*"get" + 0.012*"use" '
  '+ 0.012*"work"'),
 (38,
  '0.072*"work" + 0.068*"well" + 0.059*"good" + 0.025*"laptop" + 0.021*"need" '
  '+ 0.020*"use" + 0.018*"quality" + 0.016*"buy" + 0.015*"high" + '
  '0.015*"great"'),
 (39,
  '0.033*"laptop" + 0.017*"go" + 0.016*"get" + 0.015*"run" + 0.015*"multiple" '
  '+ 0.013*"good" + 0.013*"time" + 0.012*"take" + 0.012*"need" + '
  '0.011*"small"'),
 (41,
  '0.049*"good" + 0.048*"fast" + 0.022*"super" + 0.022*"computer" + '
  '0.020*"new" + 0.019*"love" + 0.01

In [6]:
import pickle

lda_model_file = f'{folder1}LDA_model.model' 
loaded_lda_model = pickle.load(open(lda_model_file, 'rb')) #load trained model

loaded_dictionary = pickle.load(open(f'{folder1}LDA_model.dict', 'rb')) #load dictionary 
loaded_corpus = pickle.load(open(f'{folder1}LDA_model.corpus', 'rb')) # load corpus
